**Project gutenberg**:scraping the few author articles from project Gutenberg and Predicting  the Author of the article.

In [59]:
import pandas as pd
import re
import urllib.request as url
from urllib.request import urlopen
from urllib.error import HTTPError
from urllib.error import URLError
from bs4 import BeautifulSoup

In [47]:
from selenium import webdriver
from selenium.webdriver.support import expected_conditions as ec
from selenium.webdriver.support.wait import WebDriverWait
from selenium.webdriver.common.by import By
import time
import pandas as pd

try:
    Author_Dict={}
    Author_Name_list=[]
    Books_Name=[]
    Books_links=[]
    #str_1="Dickens, Charles, 1812-1870"
    #print(str_1.find('Dickens, Charles (3918)'))
    driver=webdriver.Chrome(r"E:\chromedriver_win32\chromedriver.exe")
    driver.maximize_window()
    driver.get("https://www.gutenberg.org/")
    browse_catalog=driver.find_element_by_id("gutSearchBody")
    values=browse_catalog.find_elements_by_tag_name('li')
    element_to_be_Clicked=None
    for i in values:
        if(str(i.text).lower()=='browse catalog'):
            element_to_be_Clicked=i
    if(element_to_be_Clicked):
        element_to_be_Clicked.click()
    else:
        raise Exception('Browse Catalog element not found')
    time.sleep(20)
    Top100=WebDriverWait(driver,60).until(ec.presence_of_element_located((By.XPATH,'/html/body/div[2]/div[3]/p[5]/a')))
    Top100.click()
    #values=ele.find_elements_by_tag_name('a')
    #is_Clicked=False
    #driver.implicitly_wait(15)
    #for i in values:
        #if(i.text.lower()=='top 100'):
            #i.click()
            #is_Clicked=True
           # break
    #if(not is_Clicked):
       # raise Exception('Unable to locate  the Top 100 element')
    time.sleep(20)
    #/html/body/div[2]/div[3]/p[5]/a
    Top100Yesterday=WebDriverWait(driver,10).until(ec.presence_of_element_located((By.XPATH,'/html/body/div[2]/div[3]/p[2]/a[2]')))
    Top100Yesterday.click()
    print("Top100 AUthors Yesterday clicked successfully")
    count=0
    i=0
    while(i<100 and count<2):
        time.sleep(10)
        ele=WebDriverWait(driver,10).until(ec.presence_of_element_located((By.XPATH,'/html/body/div[2]/div[3]/ol[2]')))
        PopularAuthors=ele.find_elements_by_tag_name('a')[i]
        Books_link_dict={}
        index_1=PopularAuthors.text.find('(')
        AuthorName=PopularAuthors.text[0:index_1].strip()
        #Author_Dict.update({PopularAuthors.text[0:index_1].strip():""})
        PopularAuthors.click()
        BooksPage=WebDriverWait(driver,10).until(ec.presence_of_element_located((By.CLASS_NAME,'pgdbbyauthor')))
        alltags=BooksPage.find_elements(By.XPATH,'.//*')
        h2tags=BooksPage.find_elements_by_tag_name('h2')
        for j in h2tags:
            if(j.text.lower().find(AuthorName.lower())>-1):
                element=j
                break
        index=alltags.index(element)
        liwebElements=alltags[index+3].find_elements_by_tag_name('li')
        if(len(liwebElements)>=100):
            count+=1
            for k in range(0,101):
                atags=liwebElements[k].find_elements_by_tag_name('a')
                for l in atags:
                    if('wikipedia' not in l.text.lower()):
                        if(l.text not in Books_Name):
                            Books_Name.append(l.text)
                            Books_links.append(l.get_attribute('href'))
                            Author_Name_list.append(AuthorName)
                    #Books_link_dict.update({l.text:l.get_attribute('href')})
            Author_Dict.update({"AuthorName":Author_Name_list,"BooksName":Books_Name,"Links":Books_links})
        driver.back()
        i+=1
        
    print(Author_Dict)
   
except Exception as ex:
    print(ex)
finally:
    driver.quit()

Top100 AUthors Yesterday clicked successfully
{'AuthorName': ['Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles', 'Dickens, Charles'

FileNotFoundError: [Errno 2] No such file or directory: 'D:\\Books\\Author_Books.xlsx'

In [48]:
df=pd.DataFrame.from_dict(Author_Dict)

In [49]:
df.to_csv("Books_Links.csv",index=False)

In [72]:
data = pd.read_csv("Books_links.csv")

In [73]:
data.head()

AuthorName                                BooksName  \
0  Dickens, Charles                                  L'abîme   
1  Dickens, Charles                       All the Year Round   
2  Dickens, Charles                           American Notes   
3  Dickens, Charles   Aventures de Monsieur Pickwick, Vol. I   
4  Dickens, Charles  Aventures de Monsieur Pickwick, Vol. II   

                                    Links  
0  https://www.gutenberg.org/ebooks/18059  
1   https://www.gutenberg.org/ebooks/9691  
2    https://www.gutenberg.org/ebooks/675  
3  https://www.gutenberg.org/ebooks/13771  
4  https://www.gutenberg.org/ebooks/14789

In [74]:
data.AuthorName.nunique()

2

In [75]:
data.AuthorName.value_counts()

Dickens, Charles       75
Doyle, Arthur Conan    73
Name: AuthorName, dtype: int64

Getting text links and text from urls

In [76]:
def func(text):
    return re.sub(r'^/','https://www.gutenberg.org/', text)

data['Links']= data['Links'].apply(func)

In [77]:
def txtlink(links):
  ul = []
  for url in links:
    reqs = urlopen(url).read()
    soup = BeautifulSoup(reqs)
    for link in soup.find_all('a', attrs={'href': re.compile(".txt.utf-8$|.txt$")}):
      ul.append(link['href'])
      print(ul)
  return ul

In [78]:
txt = txtlink(data['Links'])

['/ebooks/18059.txt.utf-8']
['/ebooks/18059.txt.utf-8', '/files/9691/9691-readme.txt']
['/ebooks/18059.txt.utf-8', '/files/9691/9691-readme.txt', '/files/675/675-0.txt']
['/ebooks/18059.txt.utf-8', '/files/9691/9691-readme.txt', '/files/675/675-0.txt', '/ebooks/13771.txt.utf-8']
['/ebooks/18059.txt.utf-8', '/files/9691/9691-readme.txt', '/files/675/675-0.txt', '/ebooks/13771.txt.utf-8', '/ebooks/14789.txt.utf-8']
['/ebooks/18059.txt.utf-8', '/files/9691/9691-readme.txt', '/files/675/675-0.txt', '/ebooks/13771.txt.utf-8', '/ebooks/14789.txt.utf-8', '/ebooks/37093.txt.utf-8']
['/ebooks/18059.txt.utf-8', '/files/9691/9691-readme.txt', '/files/675/675-0.txt', '/ebooks/13771.txt.utf-8', '/ebooks/14789.txt.utf-8', '/ebooks/37093.txt.utf-8', '/ebooks/25985.txt.utf-8']
['/ebooks/18059.txt.utf-8', '/files/9691/9691-readme.txt', '/files/675/675-0.txt', '/ebooks/13771.txt.utf-8', '/ebooks/14789.txt.utf-8', '/ebooks/37093.txt.utf-8', '/ebooks/25985.txt.utf-8', '/ebooks/17879.txt.utf-8']
['/ebooks/

['/ebooks/18059.txt.utf-8', '/files/9691/9691-readme.txt', '/files/675/675-0.txt', '/ebooks/13771.txt.utf-8', '/ebooks/14789.txt.utf-8', '/ebooks/37093.txt.utf-8', '/ebooks/25985.txt.utf-8', '/ebooks/17879.txt.utf-8', '/ebooks/17880.txt.utf-8', '/files/9732/9732-readme.txt', '/files/917/917-0.txt', '/files/24501/24501-0.txt', '/files/676/676-0.txt', '/ebooks/40723.txt.utf-8', '/ebooks/44578.txt.utf-8', '/files/46804/46804-0.txt', '/ebooks/1023.txt.utf-8', '/ebooks/28198.txt.utf-8', '/ebooks/16021.txt.utf-8', '/ebooks/23765.txt.utf-8', '/ebooks/37121.txt.utf-8', '/files/42232/42232-0.txt', '/ebooks/699.txt.utf-8', '/files/9738/9738-readme.txt', '/files/19505/19505.txt', '/files/46/46-0.txt']
['/ebooks/18059.txt.utf-8', '/files/9691/9691-readme.txt', '/files/675/675-0.txt', '/ebooks/13771.txt.utf-8', '/ebooks/14789.txt.utf-8', '/ebooks/37093.txt.utf-8', '/ebooks/25985.txt.utf-8', '/ebooks/17879.txt.utf-8', '/ebooks/17880.txt.utf-8', '/files/9732/9732-readme.txt', '/files/917/917-0.txt', 

['/ebooks/18059.txt.utf-8', '/files/9691/9691-readme.txt', '/files/675/675-0.txt', '/ebooks/13771.txt.utf-8', '/ebooks/14789.txt.utf-8', '/ebooks/37093.txt.utf-8', '/ebooks/25985.txt.utf-8', '/ebooks/17879.txt.utf-8', '/ebooks/17880.txt.utf-8', '/files/9732/9732-readme.txt', '/files/917/917-0.txt', '/files/24501/24501-0.txt', '/files/676/676-0.txt', '/ebooks/40723.txt.utf-8', '/ebooks/44578.txt.utf-8', '/files/46804/46804-0.txt', '/ebooks/1023.txt.utf-8', '/ebooks/28198.txt.utf-8', '/ebooks/16021.txt.utf-8', '/ebooks/23765.txt.utf-8', '/ebooks/37121.txt.utf-8', '/files/42232/42232-0.txt', '/ebooks/699.txt.utf-8', '/files/9738/9738-readme.txt', '/files/19505/19505.txt', '/files/46/46-0.txt', '/ebooks/41739.txt.utf-8', '/ebooks/30368.txt.utf-8', '/ebooks/41894.txt.utf-8', '/ebooks/16022.txt.utf-8', '/files/1464/1464-0.txt', '/files/9739/9739-readme.txt', '/ebooks/20795.txt.utf-8', '/ebooks/37581.txt.utf-8', '/files/49683/49683-0.txt', '/files/9744/9744-readme.txt']
['/ebooks/18059.txt.ut

['/ebooks/18059.txt.utf-8', '/files/9691/9691-readme.txt', '/files/675/675-0.txt', '/ebooks/13771.txt.utf-8', '/ebooks/14789.txt.utf-8', '/ebooks/37093.txt.utf-8', '/ebooks/25985.txt.utf-8', '/ebooks/17879.txt.utf-8', '/ebooks/17880.txt.utf-8', '/files/9732/9732-readme.txt', '/files/917/917-0.txt', '/files/24501/24501-0.txt', '/files/676/676-0.txt', '/ebooks/40723.txt.utf-8', '/ebooks/44578.txt.utf-8', '/files/46804/46804-0.txt', '/ebooks/1023.txt.utf-8', '/ebooks/28198.txt.utf-8', '/ebooks/16021.txt.utf-8', '/ebooks/23765.txt.utf-8', '/ebooks/37121.txt.utf-8', '/files/42232/42232-0.txt', '/ebooks/699.txt.utf-8', '/files/9738/9738-readme.txt', '/files/19505/19505.txt', '/files/46/46-0.txt', '/ebooks/41739.txt.utf-8', '/ebooks/30368.txt.utf-8', '/ebooks/41894.txt.utf-8', '/ebooks/16022.txt.utf-8', '/files/1464/1464-0.txt', '/files/9739/9739-readme.txt', '/ebooks/20795.txt.utf-8', '/ebooks/37581.txt.utf-8', '/files/49683/49683-0.txt', '/files/9744/9744-readme.txt', '/ebooks/18186.txt.utf

['/ebooks/18059.txt.utf-8', '/files/9691/9691-readme.txt', '/files/675/675-0.txt', '/ebooks/13771.txt.utf-8', '/ebooks/14789.txt.utf-8', '/ebooks/37093.txt.utf-8', '/ebooks/25985.txt.utf-8', '/ebooks/17879.txt.utf-8', '/ebooks/17880.txt.utf-8', '/files/9732/9732-readme.txt', '/files/917/917-0.txt', '/files/24501/24501-0.txt', '/files/676/676-0.txt', '/ebooks/40723.txt.utf-8', '/ebooks/44578.txt.utf-8', '/files/46804/46804-0.txt', '/ebooks/1023.txt.utf-8', '/ebooks/28198.txt.utf-8', '/ebooks/16021.txt.utf-8', '/ebooks/23765.txt.utf-8', '/ebooks/37121.txt.utf-8', '/files/42232/42232-0.txt', '/ebooks/699.txt.utf-8', '/files/9738/9738-readme.txt', '/files/19505/19505.txt', '/files/46/46-0.txt', '/ebooks/41739.txt.utf-8', '/ebooks/30368.txt.utf-8', '/ebooks/41894.txt.utf-8', '/ebooks/16022.txt.utf-8', '/files/1464/1464-0.txt', '/files/9739/9739-readme.txt', '/ebooks/20795.txt.utf-8', '/ebooks/37581.txt.utf-8', '/files/49683/49683-0.txt', '/files/9744/9744-readme.txt', '/ebooks/18186.txt.utf

...

['/ebooks/18059.txt.utf-8', '/files/9691/9691-readme.txt', '/files/675/675-0.txt', '/ebooks/13771.txt.utf-8', '/ebooks/14789.txt.utf-8', '/ebooks/37093.txt.utf-8', '/ebooks/25985.txt.utf-8', '/ebooks/17879.txt.utf-8', '/ebooks/17880.txt.utf-8', '/files/9732/9732-readme.txt', '/files/917/917-0.txt', '/files/24501/24501-0.txt', '/files/676/676-0.txt', '/ebooks/40723.txt.utf-8', '/ebooks/44578.txt.utf-8', '/files/46804/46804-0.txt', '/ebooks/1023.txt.utf-8', '/ebooks/28198.txt.utf-8', '/ebooks/16021.txt.utf-8', '/ebooks/23765.txt.utf-8', '/ebooks/37121.txt.utf-8', '/files/42232/42232-0.txt', '/ebooks/699.txt.utf-8', '/files/9738/9738-readme.txt', '/files/19505/19505.txt', '/files/46/46-0.txt', '/ebooks/41739.txt.utf-8', '/ebooks/30368.txt.utf-8', '/ebooks/41894.txt.utf-8', '/ebooks/16022.txt.utf-8', '/files/1464/1464-0.txt', '/files/9739/9739-readme.txt', '/ebooks/20795.txt.utf-8', '/ebooks/37581.txt.utf-8', '/files/49683/49683-0.txt', '/files/9744/9744-readme.txt', '/ebooks/18186.txt.utf

['/ebooks/18059.txt.utf-8', '/files/9691/9691-readme.txt', '/files/675/675-0.txt', '/ebooks/13771.txt.utf-8', '/ebooks/14789.txt.utf-8', '/ebooks/37093.txt.utf-8', '/ebooks/25985.txt.utf-8', '/ebooks/17879.txt.utf-8', '/ebooks/17880.txt.utf-8', '/files/9732/9732-readme.txt', '/files/917/917-0.txt', '/files/24501/24501-0.txt', '/files/676/676-0.txt', '/ebooks/40723.txt.utf-8', '/ebooks/44578.txt.utf-8', '/files/46804/46804-0.txt', '/ebooks/1023.txt.utf-8', '/ebooks/28198.txt.utf-8', '/ebooks/16021.txt.utf-8', '/ebooks/23765.txt.utf-8', '/ebooks/37121.txt.utf-8', '/files/42232/42232-0.txt', '/ebooks/699.txt.utf-8', '/files/9738/9738-readme.txt', '/files/19505/19505.txt', '/files/46/46-0.txt', '/ebooks/41739.txt.utf-8', '/ebooks/30368.txt.utf-8', '/ebooks/41894.txt.utf-8', '/ebooks/16022.txt.utf-8', '/files/1464/1464-0.txt', '/files/9739/9739-readme.txt', '/ebooks/20795.txt.utf-8', '/ebooks/37581.txt.utf-8', '/files/49683/49683-0.txt', '/files/9744/9744-readme.txt', '/ebooks/18186.txt.utf

['/ebooks/18059.txt.utf-8', '/files/9691/9691-readme.txt', '/files/675/675-0.txt', '/ebooks/13771.txt.utf-8', '/ebooks/14789.txt.utf-8', '/ebooks/37093.txt.utf-8', '/ebooks/25985.txt.utf-8', '/ebooks/17879.txt.utf-8', '/ebooks/17880.txt.utf-8', '/files/9732/9732-readme.txt', '/files/917/917-0.txt', '/files/24501/24501-0.txt', '/files/676/676-0.txt', '/ebooks/40723.txt.utf-8', '/ebooks/44578.txt.utf-8', '/files/46804/46804-0.txt', '/ebooks/1023.txt.utf-8', '/ebooks/28198.txt.utf-8', '/ebooks/16021.txt.utf-8', '/ebooks/23765.txt.utf-8', '/ebooks/37121.txt.utf-8', '/files/42232/42232-0.txt', '/ebooks/699.txt.utf-8', '/files/9738/9738-readme.txt', '/files/19505/19505.txt', '/files/46/46-0.txt', '/ebooks/41739.txt.utf-8', '/ebooks/30368.txt.utf-8', '/ebooks/41894.txt.utf-8', '/ebooks/16022.txt.utf-8', '/files/1464/1464-0.txt', '/files/9739/9739-readme.txt', '/ebooks/20795.txt.utf-8', '/ebooks/37581.txt.utf-8', '/files/49683/49683-0.txt', '/files/9744/9744-readme.txt', '/ebooks/18186.txt.utf

['/ebooks/18059.txt.utf-8', '/files/9691/9691-readme.txt', '/files/675/675-0.txt', '/ebooks/13771.txt.utf-8', '/ebooks/14789.txt.utf-8', '/ebooks/37093.txt.utf-8', '/ebooks/25985.txt.utf-8', '/ebooks/17879.txt.utf-8', '/ebooks/17880.txt.utf-8', '/files/9732/9732-readme.txt', '/files/917/917-0.txt', '/files/24501/24501-0.txt', '/files/676/676-0.txt', '/ebooks/40723.txt.utf-8', '/ebooks/44578.txt.utf-8', '/files/46804/46804-0.txt', '/ebooks/1023.txt.utf-8', '/ebooks/28198.txt.utf-8', '/ebooks/16021.txt.utf-8', '/ebooks/23765.txt.utf-8', '/ebooks/37121.txt.utf-8', '/files/42232/42232-0.txt', '/ebooks/699.txt.utf-8', '/files/9738/9738-readme.txt', '/files/19505/19505.txt', '/files/46/46-0.txt', '/ebooks/41739.txt.utf-8', '/ebooks/30368.txt.utf-8', '/ebooks/41894.txt.utf-8', '/ebooks/16022.txt.utf-8', '/files/1464/1464-0.txt', '/files/9739/9739-readme.txt', '/ebooks/20795.txt.utf-8', '/ebooks/37581.txt.utf-8', '/files/49683/49683-0.txt', '/files/9744/9744-readme.txt', '/ebooks/18186.txt.utf

['/ebooks/18059.txt.utf-8', '/files/9691/9691-readme.txt', '/files/675/675-0.txt', '/ebooks/13771.txt.utf-8', '/ebooks/14789.txt.utf-8', '/ebooks/37093.txt.utf-8', '/ebooks/25985.txt.utf-8', '/ebooks/17879.txt.utf-8', '/ebooks/17880.txt.utf-8', '/files/9732/9732-readme.txt', '/files/917/917-0.txt', '/files/24501/24501-0.txt', '/files/676/676-0.txt', '/ebooks/40723.txt.utf-8', '/ebooks/44578.txt.utf-8', '/files/46804/46804-0.txt', '/ebooks/1023.txt.utf-8', '/ebooks/28198.txt.utf-8', '/ebooks/16021.txt.utf-8', '/ebooks/23765.txt.utf-8', '/ebooks/37121.txt.utf-8', '/files/42232/42232-0.txt', '/ebooks/699.txt.utf-8', '/files/9738/9738-readme.txt', '/files/19505/19505.txt', '/files/46/46-0.txt', '/ebooks/41739.txt.utf-8', '/ebooks/30368.txt.utf-8', '/ebooks/41894.txt.utf-8', '/ebooks/16022.txt.utf-8', '/files/1464/1464-0.txt', '/files/9739/9739-readme.txt', '/ebooks/20795.txt.utf-8', '/ebooks/37581.txt.utf-8', '/files/49683/49683-0.txt', '/files/9744/9744-readme.txt', '/ebooks/18186.txt.utf

In [82]:
txt = pd.DataFrame(txt)

In [83]:
data['txtlink'] = txt

In [84]:
data['txtlink']= data['txtlink'].apply(func)

In [86]:
import requests
text = []
for url in data['txtlink']:
  reqs = requests.get(url)
  soup = BeautifulSoup(reqs.text, 'lxml')
  print("Text from the said page:")
  text.append(soup.get_text())
  print(text)

Text from the said page:
['The Project Gutenberg EBook of L\'abîme, by Charles Dickens and Wilkie Collins\r\n\r\nThis eBook is for the use of anyone anywhere at no cost and with\r\nalmost no restrictions whatsoever.  You may copy it, give it away or\r\nre-use it under the terms of the Project Gutenberg License included\r\nwith this eBook or online at www.gutenberg.org\r\n\r\n\r\nTitle: L\'abîme\r\n\r\nAuthor: Charles Dickens and Wilkie Collins\r\n\r\nTranslator: Madame Judith de la Comédie Française\r\n\r\nRelease Date: March 27, 2006 [EBook #18059]\r\n\r\nLanguage: French\r\n\r\n\r\n*** START OF THIS PROJECT GUTENBERG EBOOK L\'ABÎME ***\r\n\r\n\r\n\r\n\r\nProduced by www.ebooksgratuits.com and Chuck Greif\r\n\r\n\r\n\r\n\r\n\r\n\r\n\r\n\r\nCharles Dickens et Wilkie Collins\r\n\r\n\r\n\r\n\r\nL\'ABÎME\r\n\r\nRoman anglais traduit avec l\'autorisation de l\'auteur par Madame Judith\r\nde la Comédie Française\r\n\r\nNouvelle édition Librairie Hachette et Cie.\r\n\r\n1918\r\n\r\n\r\n\r\n\

Text from the said page:
['The Project Gutenberg EBook of L\'abîme, by Charles Dickens and Wilkie Collins\r\n\r\nThis eBook is for the use of anyone anywhere at no cost and with\r\nalmost no restrictions whatsoever.  You may copy it, give it away or\r\nre-use it under the terms of the Project Gutenberg License included\r\nwith this eBook or online at www.gutenberg.org\r\n\r\n\r\nTitle: L\'abîme\r\n\r\nAuthor: Charles Dickens and Wilkie Collins\r\n\r\nTranslator: Madame Judith de la Comédie Française\r\n\r\nRelease Date: March 27, 2006 [EBook #18059]\r\n\r\nLanguage: French\r\n\r\n\r\n*** START OF THIS PROJECT GUTENBERG EBOOK L\'ABÎME ***\r\n\r\n\r\n\r\n\r\nProduced by www.ebooksgratuits.com and Chuck Greif\r\n\r\n\r\n\r\n\r\n\r\n\r\n\r\n\r\nCharles Dickens et Wilkie Collins\r\n\r\n\r\n\r\n\r\nL\'ABÎME\r\n\r\nRoman anglais traduit avec l\'autorisation de l\'auteur par Madame Judith\r\nde la Comédie Française\r\n\r\nNouvelle édition Librairie Hachette et Cie.\r\n\r\n1918\r\n\r\n\r\n\r\n\

Text from the said page:
['The Project Gutenberg EBook of L\'abîme, by Charles Dickens and Wilkie Collins\r\n\r\nThis eBook is for the use of anyone anywhere at no cost and with\r\nalmost no restrictions whatsoever.  You may copy it, give it away or\r\nre-use it under the terms of the Project Gutenberg License included\r\nwith this eBook or online at www.gutenberg.org\r\n\r\n\r\nTitle: L\'abîme\r\n\r\nAuthor: Charles Dickens and Wilkie Collins\r\n\r\nTranslator: Madame Judith de la Comédie Française\r\n\r\nRelease Date: March 27, 2006 [EBook #18059]\r\n\r\nLanguage: French\r\n\r\n\r\n*** START OF THIS PROJECT GUTENBERG EBOOK L\'ABÎME ***\r\n\r\n\r\n\r\n\r\nProduced by www.ebooksgratuits.com and Chuck Greif\r\n\r\n\r\n\r\n\r\n\r\n\r\n\r\n\r\nCharles Dickens et Wilkie Collins\r\n\r\n\r\n\r\n\r\nL\'ABÎME\r\n\r\nRoman anglais traduit avec l\'autorisation de l\'auteur par Madame Judith\r\nde la Comédie Française\r\n\r\nNouvelle édition Librairie Hachette et Cie.\r\n\r\n1918\r\n\r\n\r\n\r\n\

Text from the said page:
['The Project Gutenberg EBook of L\'abîme, by Charles Dickens and Wilkie Collins\r\n\r\nThis eBook is for the use of anyone anywhere at no cost and with\r\nalmost no restrictions whatsoever.  You may copy it, give it away or\r\nre-use it under the terms of the Project Gutenberg License included\r\nwith this eBook or online at www.gutenberg.org\r\n\r\n\r\nTitle: L\'abîme\r\n\r\nAuthor: Charles Dickens and Wilkie Collins\r\n\r\nTranslator: Madame Judith de la Comédie Française\r\n\r\nRelease Date: March 27, 2006 [EBook #18059]\r\n\r\nLanguage: French\r\n\r\n\r\n*** START OF THIS PROJECT GUTENBERG EBOOK L\'ABÎME ***\r\n\r\n\r\n\r\n\r\nProduced by www.ebooksgratuits.com and Chuck Greif\r\n\r\n\r\n\r\n\r\n\r\n\r\n\r\n\r\nCharles Dickens et Wilkie Collins\r\n\r\n\r\n\r\n\r\nL\'ABÎME\r\n\r\nRoman anglais traduit avec l\'autorisation de l\'auteur par Madame Judith\r\nde la Comédie Française\r\n\r\nNouvelle édition Librairie Hachette et Cie.\r\n\r\n1918\r\n\r\n\r\n\r\n\

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



...

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Text from the said page:


IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Text from the said page:


IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [87]:
data['text'] = text

In [88]:
data.head()

AuthorName                                BooksName  \
0  Dickens, Charles                                  L'abîme   
1  Dickens, Charles                       All the Year Round   
2  Dickens, Charles                           American Notes   
3  Dickens, Charles   Aventures de Monsieur Pickwick, Vol. I   
4  Dickens, Charles  Aventures de Monsieur Pickwick, Vol. II   

                                    Links  \
0  https://www.gutenberg.org/ebooks/18059   
1   https://www.gutenberg.org/ebooks/9691   
2    https://www.gutenberg.org/ebooks/675   
3  https://www.gutenberg.org/ebooks/13771   
4  https://www.gutenberg.org/ebooks/14789   

                                             txtlink  \
0   https://www.gutenberg.org/ebooks/18059.txt.utf-8   
1  https://www.gutenberg.org/files/9691/9691-read...   
2      https://www.gutenberg.org/files/675/675-0.txt   
3   https://www.gutenberg.org/ebooks/13771.txt.utf-8   
4   https://www.gutenberg.org/ebooks/14789.txt.utf-8   

                                                text  
0  The Project Gutenberg EBook of L'abîme, by Cha...  
1  The Project Gutenberg EBook of All The Year Ro...  
2  ï»¿The Project Gutenberg eBook, American Notes...  
3  Project Gutenberg's Aventures de Monsieur Pick...  
4  The Project Gutenberg EBook of Aventures de Mo...

**Text Preprocessing**

In [89]:
#LowerCase all  text
data['text'] = [text.strip().lower() for text in data['text']]
data['text'][:10]

0    the project gutenberg ebook of l'abîme, by cha...
1    the project gutenberg ebook of all the year ro...
2    ï»¿the project gutenberg ebook, american notes...
3    project gutenberg's aventures de monsieur pick...
4    the project gutenberg ebook of aventures de mo...
5    the project gutenberg ebook of de avonturen va...
6    the project gutenberg ebook, bardell v. pickwi...
7    the project gutenberg ebook of barnabé rudge, ...
8    the project gutenberg ebook of barnabé rudge, ...
9    the project gutenberg ebook of barnaby rudge, ...
Name: text, dtype: object

In [90]:
#expanding contractions
##Handling contractions

contractions = {
"ain't": "is not",
"aren't": "are not",
"can't": "cannot",
"can't've": "cannot have",
"'cause": "because",
"could've": "could have",
"couldn't": "could not",
"couldn't've": "could not have",
"didn't": "did not",
"doesn't": "does not",
"don't": "do not",
"hadn't": "had not",
"hadn't've": "had not have",
"hasn't": "has not",
"haven't": "have not",
"he'd": "he would",
"he'd've": "he would have",
"he'll": "he will",
"he'll've": "he he will have",
"he's": "he is",
"how'd": "how did",
"how'd'y": "how do you",
"how'll": "how will",
"how's": "how is",
"I'd": "I would",
"I'd've": "I would have",
"I'll": "I will",
"I'll've": "I will have",
"I'm": "I am",
"I've": "I have",
"i'd": "i would",
"i'd've": "i would have",
"i'll": "i will",
"i'll've": "i will have",
"i'm": "i am",
"i've": "i have",
"isn't": "is not",
"it'd": "it would",
"it'd've": "it would have",
"it'll": "it will",
"it'll've": "it will have",
"it's": "it is",
"let's": "let us",
"ma'am": "madam",
"mayn't": "may not",
"might've": "might have",
"mightn't": "might not",
"mightn't've": "might not have",
"must've": "must have",
"mustn't": "must not",
"mustn't've": "must not have",
"needn't": "need not",
"needn't've": "need not have",
"o'clock": "of the clock",
"oughtn't": "ought not",
"oughtn't've": "ought not have",
"shan't": "shall not",
"sha'n't": "shall not",
"shan't've": "shall not have",
"she'd": "she would",
"she'd've": "she would have",
"she'll": "she will",
"she'll've": "she will have",
"she's": "she is",
"should've": "should have",
"shouldn't": "should not",
"shouldn't've": "should not have",
"so've": "so have",
"so's": "so as",
"that'd": "that would",
"that'd've": "that would have",
"that's": "that is",
"there'd": "there would",
"there'd've": "there would have",
"there's": "there is",
"they'd": "they would",
"they'd've": "they would have",
"they'll": "they will",
"they'll've": "they will have",
"they're": "they are",
"they've": "they have",
"to've": "to have",
"wasn't": "was not",
"we'd": "we would",
"we'd've": "we would have",
"we'll": "we will",
"we'll've": "we will have",
"we're": "we are",
"we've": "we have",
"weren't": "were not",
"what'll": "what will",
"what'll've": "what will have",
"what're": "what are",
"what's": "what is",
"what've": "what have",
"when's": "when is",
"when've": "when have",
"where'd": "where did",
"where's": "where is",
"where've": "where have",
"who'll": "who will",
"who'll've": "who will have",
"who's": "who is",
"who've": "who have",
"why's": "why is",
"why've": "why have",
"will've": "will have",
"won't": "will not",
"won't've": "will not have",
"would've": "would have",
"wouldn't": "would not",
"wouldn't've": "would not have",
"y'all": "you all",
"y'all'd": "you all would",
"y'all'd've": "you all would have",
"y'all're": "you all are",
"y'all've": "you all have",
"you'd": "you would",
"you'd've": "you would have",
"you'll": "you will",
"you'll've": "you will have",
"you're": "you are",
"you've": "you have"}

In [91]:
def expand_contractions(text):
    for word in text.split():
        if word.lower() in contractions:
            text = text.replace(word, contractions[word.lower()])
    return text

In [92]:
data['text'] = data['text'].astype(str)

In [93]:
data['text'] = [expand_contractions(re.sub('’', "'", text)) for text in data['text']]
data['text'][0]

'the project gutenberg ebook of l\'abîme, by charles dickens and wilkie collins\r\n\r\nthis ebook is for the use of anyone anywhere at no cost and with\r\nalmost no restrictions whatsoever.  you may copy it, give it away or\r\nre-use it under the terms of the project gutenberg license included\r\nwith this ebook or online at www.gutenberg.org\r\n\r\n\r\ntitle: l\'abîme\r\n\r\nauthor: charles dickens and wilkie collins\r\n\r\ntranslator: madame judith de la comédie française\r\n\r\nrelease date: march 27, 2006 [ebook #18059]\r\n\r\nlanguage: french\r\n\r\n\r\n*** start of this project gutenberg ebook l\'abîme ***\r\n\r\n\r\n\r\n\r\nproduced by www.ebooksgratuits.com and chuck greif\r\n\r\n\r\n\r\n\r\n\r\n\r\n\r\n\r\ncharles dickens et wilkie collins\r\n\r\n\r\n\r\n\r\nl\'abîme\r\n\r\nroman anglais traduit avec l\'autorisation de l\'auteur par madame judith\r\nde la comédie française\r\n\r\nnouvelle édition librairie hachette et cie.\r\n\r\n1918\r\n\r\n\r\n\r\n\r\ntable des matières\r\n\

In [94]:
#removing_accented_chars
#https://docs.python.org/2/library/unicodedata.html
import unicodedata
def remove_accented_chars(text):
    text = unicodedata.normalize('NFKD', text).encode('ascii', 'ignore').decode('utf-8', 'ignore')
    return text

In [95]:
data['text'] = [remove_accented_chars(text) for text in data['text']]
data['text'][0]

'the project gutenberg ebook of l\'abime, by charles dickens and wilkie collins\r\n\r\nthis ebook is for the use of anyone anywhere at no cost and with\r\nalmost no restrictions whatsoever.  you may copy it, give it away or\r\nre-use it under the terms of the project gutenberg license included\r\nwith this ebook or online at www.gutenberg.org\r\n\r\n\r\ntitle: l\'abime\r\n\r\nauthor: charles dickens and wilkie collins\r\n\r\ntranslator: madame judith de la comedie francaise\r\n\r\nrelease date: march 27, 2006 [ebook #18059]\r\n\r\nlanguage: french\r\n\r\n\r\n*** start of this project gutenberg ebook l\'abime ***\r\n\r\n\r\n\r\n\r\nproduced by www.ebooksgratuits.com and chuck greif\r\n\r\n\r\n\r\n\r\n\r\n\r\n\r\n\r\ncharles dickens et wilkie collins\r\n\r\n\r\n\r\n\r\nl\'abime\r\n\r\nroman anglais traduit avec l\'autorisation de l\'auteur par madame judith\r\nde la comedie francaise\r\n\r\nnouvelle edition librairie hachette et cie.\r\n\r\n1918\r\n\r\n\r\n\r\n\r\ntable des matieres\r\n\

In [96]:
#Invoking various scrub functions
def scrub_words(text):
    #Replace \xao characters in text
    text = re.sub('\xa0', ' ', text)
    
    #Replace non ascii / not words and digits
    text = re.sub("(\\W|\\d)",' ',text)
    
    #Replace new line characters and following text untill space
    text = re.sub('\n(\w*?)[\s]', '', text)
    
    #Remove html markup
    text = re.sub("<.*?>", ' ', text)
    
    #Remove extra spaces from the text
    text = re.sub("\s+", ' ', text)
    return text

In [97]:
data['text'] = [scrub_words(text) for text in data['text']]
data['text'][0]

'the project gutenberg ebook of l abime by charles dickens and wilkie collins this ebook is for the use of anyone anywhere at no cost and with almost no restrictions whatsoever you may copy it give it away or re use it under the terms of the project gutenberg license included with this ebook or online at www gutenberg org title l abime author charles dickens and wilkie collins translator madame judith de la comedie francaise release date march ebook language french start of this project gutenberg ebook l abime produced by www ebooksgratuits com and chuck greif charles dickens et wilkie collins l abime roman anglais traduit avec l autorisation de l auteur par madame judith de la comedie francaise nouvelle edition librairie hachette et cie table des matieres ouverture premier acte le rideau se leve la femme de charge entre la femme de charge parle nouveaux personnages en scene sortie de wilding deuxieme acte vendale se declare vendale se decide troisieme acte dans la vallee sur la montag

In [98]:
data.head()

AuthorName                                BooksName  \
0  Dickens, Charles                                  L'abîme   
1  Dickens, Charles                       All the Year Round   
2  Dickens, Charles                           American Notes   
3  Dickens, Charles   Aventures de Monsieur Pickwick, Vol. I   
4  Dickens, Charles  Aventures de Monsieur Pickwick, Vol. II   

                                    Links  \
0  https://www.gutenberg.org/ebooks/18059   
1   https://www.gutenberg.org/ebooks/9691   
2    https://www.gutenberg.org/ebooks/675   
3  https://www.gutenberg.org/ebooks/13771   
4  https://www.gutenberg.org/ebooks/14789   

                                             txtlink  \
0   https://www.gutenberg.org/ebooks/18059.txt.utf-8   
1  https://www.gutenberg.org/files/9691/9691-read...   
2      https://www.gutenberg.org/files/675/675-0.txt   
3   https://www.gutenberg.org/ebooks/13771.txt.utf-8   
4   https://www.gutenberg.org/ebooks/14789.txt.utf-8   

                                                text  
0  the project gutenberg ebook of l abime by char...  
1  the project gutenberg ebook of all the year ro...  
2  ithe project gutenberg ebook american notes fo...  
3  project gutenberg s aventures de monsieur pick...  
4  the project gutenberg ebook of aventures de mo...

In [99]:
# Removing numbers in the articles
data['text'] = data['text'].str.replace('\d+','')

In [100]:
# Removing mail id's from the articles
data['text'] = data['text'].str.replace("[a-zA-Z0-9_.+-]+@[a-zA-Z0-9-]+\\.[a-zA-Z0-9-.]+", "")
data['text'] = data['text'].str.replace("<@[a-zA-Z0-9-]+.[a-zA-Z0-9-.]+.[a-zA-Z0-9-.]+", "")

In [101]:
## Removing the stop words from the data
from nltk.corpus import stopwords
sw = stopwords.words('english')
sw_mr = data['text'].apply(lambda x: " ".join(x for x in x.split() if x not in sw))

In [102]:
#Tokenization
from nltk.tokenize import sent_tokenize, word_tokenize
from nltk.stem import WordNetLemmatizer 
lemmatizer = WordNetLemmatizer()
words_tokenized = [[w.lower() for w in word_tokenize(t)] for t in sw_mr]

In [103]:
data['text'] = words_tokenized

In [107]:
data['text'] = data['text'].map(
    lambda wl: [lemmatizer.lemmatize(w) for w in wl]
)

In [108]:
data.head()

AuthorName                                BooksName  \
0  Dickens, Charles                                  L'abîme   
1  Dickens, Charles                       All the Year Round   
2  Dickens, Charles                           American Notes   
3  Dickens, Charles   Aventures de Monsieur Pickwick, Vol. I   
4  Dickens, Charles  Aventures de Monsieur Pickwick, Vol. II   

                                    Links  \
0  https://www.gutenberg.org/ebooks/18059   
1   https://www.gutenberg.org/ebooks/9691   
2    https://www.gutenberg.org/ebooks/675   
3  https://www.gutenberg.org/ebooks/13771   
4  https://www.gutenberg.org/ebooks/14789   

                                             txtlink  \
0   https://www.gutenberg.org/ebooks/18059.txt.utf-8   
1  https://www.gutenberg.org/files/9691/9691-read...   
2      https://www.gutenberg.org/files/675/675-0.txt   
3   https://www.gutenberg.org/ebooks/13771.txt.utf-8   
4   https://www.gutenberg.org/ebooks/14789.txt.utf-8   

                                                text  
0  [project, gutenberg, ebook, l, abime, charles,...  
1  [project, gutenberg, ebook, year, round, charl...  
2  [ithe, project, gutenberg, ebook, american, no...  
3  [project, gutenberg, aventures, de, monsieur, ...  
4  [project, gutenberg, ebook, aventures, de, mon...

**TF-IDF**

In [112]:
# Creating the TF-IDF
from sklearn.feature_extraction.text import TfidfVectorizer
data['text']=[" ".join(text) for text in data['text'].values]


In [113]:
tfidf = TfidfVectorizer(stop_words = 'english', lowercase = True, decode_error = 'ignore',min_df=0.01, max_df=0.99)

In [114]:
df_tfidf = tfidf.fit_transform(data['text'])

In [115]:
df_tfidf.shape

(148, 101033)

**SVD**

In [122]:
# SVD
from sklearn.decomposition import TruncatedSVD
svd_model = TruncatedSVD(n_components=148, algorithm='randomized', n_iter=100, random_state=122)

In [123]:
svd_model.fit(df_tfidf)

TruncatedSVD(algorithm='randomized', n_components=148, n_iter=100,
             random_state=122, tol=0.0)

In [124]:
svd_matrix = svd_model.transform(df_tfidf)

In [125]:
#new data with 148 features instead of 101033
train_data=pd.DataFrame(svd_matrix)

In [126]:
train_data.head()

0         1         2         3         4         5         6    \
0  0.052587 -0.047497  0.901929 -0.263931 -0.000163 -0.038010 -0.003736   
1  0.052533  0.749354  0.036139 -0.002026 -0.446140 -0.002424 -0.006096   
2  0.738496 -0.016932 -0.028966 -0.008328 -0.001895 -0.014463  0.012616   
3  0.056773 -0.048637  0.919398 -0.272775 -0.000398 -0.034968  0.007852   
4  0.056615 -0.048723  0.920519 -0.271543 -0.000495 -0.024952  0.008329   

        7         8         9    ...       138       139       140       141  \
0 -0.014545 -0.066383 -0.007220  ... -0.005698  0.002580 -0.000801 -0.000891   
1  0.003976  0.001035 -0.026411  ... -0.000048  0.000098  0.000020 -0.000366   
2 -0.103868  0.028909 -0.162745  ...  0.000314 -0.000096 -0.000129 -0.000315   
3 -0.006416 -0.077440 -0.018785  ...  0.002988 -0.030263 -0.057846 -0.004675   
4 -0.002292 -0.068236 -0.016120  ... -0.000290  0.033581  0.057857  0.006280   

        142       143       144       145       146       147  
0 -0.002151 -0.001052  0.003979 -0.000301  0.000111  0.000140  
1  0.000156 -0.000057 -0.000014  0.000078  0.000204  0.000054  
2  0.000215  0.000296  0.000049  0.000016  0.000328  0.000070  
3 -0.005368  0.001428 -0.004253  0.000584 -0.000703 -0.000197  
4  0.006991 -0.002264 -0.001252  0.000391  0.000768  0.000198  

[5 rows x 148 columns]

In [129]:
train_data['target']=data['AuthorName']

In [130]:
train_data.shape

(148, 149)

**Splitting data**

In [132]:
from sklearn.model_selection import train_test_split
y = train_data["target"]
X = train_data.drop(['target'],axis=1)
X_train, X_val, y_train, y_val = train_test_split(X, y, test_size=0.2,random_state=666)

In [133]:
print(X_train.shape)
print(X_val.shape)
print(y_train.shape)
print(y_val.shape)

(118, 148)
(30, 148)
(118,)
(30,)


**Support vector machines**

In [135]:
from sklearn.svm import SVC
classifier= SVC()

In [136]:
classifier.fit(X_train,y_train)

SVC(C=1.0, break_ties=False, cache_size=200, class_weight=None, coef0=0.0,
    decision_function_shape='ovr', degree=3, gamma='scale', kernel='rbf',
    max_iter=-1, probability=False, random_state=None, shrinking=True,
    tol=0.001, verbose=False)

In [138]:
#prediction of train
y_pred1=classifier.predict(X_train)
#prediction of val
y_pred2=classifier.predict(X_val)

In [139]:
#confusion matrix
from sklearn.metrics import confusion_matrix
print(confusion_matrix(y_train,y_pred1))
print(confusion_matrix(y_val,y_pred2))

[[57  4]
 [ 8 49]]
[[12  2]
 [ 6 10]]


In [140]:
from sklearn.metrics import classification_report

print("Classification Report on Train Data")
print(classification_report(y_train,y_pred1))

print("Classification Report on Test Data")
print(classification_report(y_val,y_pred2))

Classification Report on Train Data
                     precision    recall  f1-score   support

   Dickens, Charles       0.88      0.93      0.90        61
Doyle, Arthur Conan       0.92      0.86      0.89        57

           accuracy                           0.90       118
          macro avg       0.90      0.90      0.90       118
       weighted avg       0.90      0.90      0.90       118

Classification Report on Test Data
                     precision    recall  f1-score   support

   Dickens, Charles       0.67      0.86      0.75        14
Doyle, Arthur Conan       0.83      0.62      0.71        16

           accuracy                           0.73        30
          macro avg       0.75      0.74      0.73        30
       weighted avg       0.76      0.73      0.73        30



**DecisionTreeClassifier**

In [142]:
from sklearn.tree import DecisionTreeClassifier  
DCT= DecisionTreeClassifier(criterion='entropy', random_state=580)  
DCT.fit(X_train, y_train) 

DecisionTreeClassifier(ccp_alpha=0.0, class_weight=None, criterion='entropy',
                       max_depth=None, max_features=None, max_leaf_nodes=None,
                       min_impurity_decrease=0.0, min_impurity_split=None,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, presort='deprecated',
                       random_state=580, splitter='best')

In [144]:
#prediction of train
y_pred3=DCT.predict(X_train)
#prediction of val
y_pred4=DCT.predict(X_val)

In [145]:
#confusion matrix
from sklearn.metrics import confusion_matrix
print(confusion_matrix(y_train,y_pred3))
print(confusion_matrix(y_val,y_pred4))

[[61  0]
 [ 0 57]]
[[13  1]
 [ 5 11]]


In [146]:
from sklearn.metrics import classification_report

print("Classification Report on Train Data")
print(classification_report(y_train,y_pred3))

print("Classification Report on Test Data")
print(classification_report(y_val,y_pred4))

Classification Report on Train Data
                     precision    recall  f1-score   support

   Dickens, Charles       1.00      1.00      1.00        61
Doyle, Arthur Conan       1.00      1.00      1.00        57

           accuracy                           1.00       118
          macro avg       1.00      1.00      1.00       118
       weighted avg       1.00      1.00      1.00       118

Classification Report on Test Data
                     precision    recall  f1-score   support

   Dickens, Charles       0.72      0.93      0.81        14
Doyle, Arthur Conan       0.92      0.69      0.79        16

           accuracy                           0.80        30
          macro avg       0.82      0.81      0.80        30
       weighted avg       0.83      0.80      0.80        30

